Kütüphane

In [1]:
from datasets import load_dataset
import pandas as pd 
from pymongo import MongoClient
from transformers import BertTokenizer, BertForMaskedLM, DPRContextEncoderTokenizer,DPRContextEncoder;
from sklearn.feature_extraction.text import TfidfVectorizer
import numpy as np
import re
import pandas as pd
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords as nltk_stopwords
from transformers import BertTokenizer, BertModel
from sklearn.metrics.pairwise import cosine_similarity
import torch
from pymongo import MongoClient
import torch.nn.functional as F



Turkish stop wordslerin tanımlanması

In [2]:
""""""
#- burada turkish_stop_words'ü alıyoruz
def load_stop_words(file_path, existing_stop_words='gereksiz_kelimeler.txt'):
    """Stop words'leri dosyadan okuyarak bir liste oluşturur. 
    Mevcut stop words'ler varsa bunları dikkate alır."""
    
    if existing_stop_words is None:
        existing_stop_words = set()
    else:
        existing_stop_words = set(existing_stop_words)
    
    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            word = line.strip()
            if word and word not in existing_stop_words:
                existing_stop_words.add(word)
    
    return list(existing_stop_words)

# Mevcut stop words'leri kontrol ederek Türkçe stop words dosyasını yükleyin
stop_words_list = load_stop_words('gereksiz_kelimeler.txt')

#----------------------------------------------------------------------------------------------------

MongoDb'deki combined_text koleksiyonunun verilerini csv ye çekme 

In [ ]:
#mongodb üzerinden combined_textleri çek
import csv
from pymongo import MongoClient

def mongo_db_combined_texts_to_csv(database_name='combined_text', collection_name='text', host='localhost', port=27017,batch_size=100,output_file='combined_texts.csv'):
    client = MongoClient(f'mongodb://{host}:{port}/')
    db = client[database_name]
    collection = db[collection_name]
    
    #toplam döküman sayısını al
    total_documents = collection.count_documents({})
    #batch_documents = []

    # CSV dosyasını aç ve yazmaya hazırla
    with open(output_file, mode='w', newline='', encoding='utf-8') as file:
        writer = csv.writer(file)
        writer.writerow(["combined"])  # CSV başlığı

    # Belirtilen batch_size kadar dökümanları almak için döngü
    for i in range(0, total_documents, batch_size):
        cursor = collection.find({}, {"combined":1, "_id": 0}).skip(i).limit(batch_size)
        combined_texts = [doc['combined'] for doc in cursor if 'combined' in doc] #combined sütununa ilişkin verileri çeker 

        # Batch verilerini CSV'ye yaz
        with open(output_file, mode='a', newline='', encoding='utf-8') as file:
            writer = csv.writer(file)
            
            for text in combined_texts:
                writer.writerow([text])
        
        

    print(f"combined metinler '{output_file}' dosyasına başarıyla yazıldı.")

# Dökümanları CSV dosyasına yazdır
text=mongo_db_combined_texts_to_csv(batch_size=100)
        #batch_documents.extend((combined_texts, len(combined_texts)))
    #append fonksiyonu listenin içerisine tek bir eleman gibi ekler yani list1 = [1, 2, 3, [4, 5]]
    #fakat extend fonksiyonu list1 = [1, 2, 3, 4, 5] bir listeye yeni bir liste eklemeyi teker teker gerçekleştirir.
    #return batch_documents

# Dökümanları ve döküman sayısını batch olarak çekin
#combined_texts = mongo_db_combined_texts(batch_size=1000)

# Her batch'i ayrı ayrı işleyebilirsiniz
#print(f"Toplam döküman sayısı:{len(combined_texts)}")

#for index, text in enumerate (combined_texts[:10]):
    #print(f"Döküman {index + 1}: {text}")

#print(combined_texts)

    

Metinleri Kısaltma Fonksiyonu (processed_data kaydetme)

In [ ]:
import csv
from pymongo import MongoClient
import pandas as pd

def fetch_from_database(database_name='combined_text', collection_name='text', host='localhost', port=27017, batch_size=100):
    client = MongoClient(f'mongodb://{host}:{port}/')
    db = client[database_name]
    collection = db[collection_name]
    
    # Toplam döküman sayısını al
    total_documents = collection.count_documents({})
    combined_texts = []

    # Belirtilen batch_size kadar dökümanları almak için döngü
    for i in range(0, total_documents, batch_size):
        cursor = collection.find({}, {"combined": 1, "_id": 0}).skip(i).limit(batch_size)
        combined_texts.extend([doc['combined'] for doc in cursor if 'combined' in doc])  # combined sütununa ilişkin verileri çeker 

    return combined_texts

# Metinleri kısaltma fonksiyonu
def truncate_text(text, max_words=300):
    words = text.split()  # Metni kelimelere böler
    return ' '.join(words[:max_words])  # İlk max_words kadar kelimeyi alır

# Veritabanından veri çekme ve kısaltma
def fetch_and_truncate_data(database_name, collection_name, host, port, max_words=300):
    # Veritabanından veri çekme
    combined_texts = fetch_from_database(database_name, collection_name, host, port)
    
    # Metinleri kısaltma
    truncated_texts = [truncate_text(text, max_words) for text in combined_texts]
    
    return truncated_texts

# Kısaltılmış veriyi CSV'ye kaydetme
def save_to_csv(data, file_path):
    df = pd.DataFrame(data, columns=['combined'])
    df.to_csv(file_path, encoding='utf-8', index=False)

# Doğru değişken tanımlamaları
database_name = 'combined_text'
collection_name = 'text'
host = 'localhost'
port = 27017
batch_size = 100
max_words = 300
output_file = 'processed_data.csv'

# Veriyi çekme ve işleme
truncated_texts = fetch_and_truncate_data(database_name, collection_name, host, port, max_words)
save_to_csv(truncated_texts, output_file)


Tf-Idf ile keywordsleri alma 

In [9]:
import re 
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from joblib import Parallel, delayed
from tqdm import tqdm
import csv



# CSV dosyasını okuma
df = pd.read_csv('processed_data.csv')
combined = df['combined'].tolist()


def pad_or_truncate(texts,max_lenght):
    "metinleri belirli bir uzunluğua kısaltır ve padler"
    padded_texts=[]
    for text in texts:
        words= text.split()
        if len(words)> max_lenght:
            padded_texts.append(''.join(words[:max_lenght]))
        else:
            padded_texts.append(' '.join(words + [''] * (max_length - len(words))))
    return padded_texts

# Padding uzunluğu
max_length = 300  # Örneğin, metin uzunluğunu 300 kelimeyle sınırlandırma

# Metinleri pad etme veya kısaltma
combined_padded = pad_or_truncate(combined, max_length)

def parse_text(text):
    """Verilen metni ayrıştırarak düzenli bir yapıya dönüştürür."""
    # Satırları ayır
    lines = text.split('|-')
    
    data = []
    for line in lines:
        line = line.strip()
        if not line or line.startswith("align"):
            continue

        # Satırı parçalara ayır
        parts = re.split(r'\s*\|\s*', line) #satırları nasıl parçalara ayırır ??
        
        # Verileri temizle ve yapıyı oluştur
        if len(parts) >= 2: # season ve team neler ve neden değişken olarak tanadı.
            season = parts[0].strip()
            team = parts[1].strip()
            stats = [p.strip() for p in parts[2:] if p.strip()]
            data.append([season, team] + stats)

    return data 

def clean_data(file_path):
    """CSV dosyasını okur ve veriyi düzenler."""
    with open(file_path, 'r',encoding='utf-8') as file:
        raw_text = file.read()
    
    data = parse_text(raw_text)
    
    # Veri çerçevesi oluştur
    df = pd.DataFrame(data)
    
    return df

# CSV dosyasını temizleyip düzenli bir DataFrame oluştur
cleaned_df = clean_data('processed_data.csv')

# Düzenlenmiş veriyi kontrol et
print(cleaned_df.head())

def extract_keywords_tfidf(combined, stop_words_list, top_n=10, n_jobs=-1):
    """TF-IDF ile anahtar kelimeleri çıkarır, stop words listesi ile birlikte kullanır ve paralel işlem yapar."""
    vectorizer = TfidfVectorizer(stop_words=stop_words_list)
    
    # TF-IDF matrisini oluşturma (CPU kullanımını optimize etmek için n_jobs kullanılır)
    X = vectorizer.fit_transform(combined)  # bunu csv'den oku
    feature_names = vectorizer.get_feature_names_out()  # Her kelimenin tf-idf vektöründeki karşılığını tutar

    # Her döküman için en iyi keywords'leri ve tf-idf değerlerini paralel işlemeyle bulma
    def process_row(row):
        tfidf_scores = row.toarray().flatten()  # Düz bir değişken haline getirme
        top_indices = tfidf_scores.argsort()[-top_n:][::-1]  # En yüksek n skoru bul
        
        # En yüksek skorlu kelimeleri ve skorları bul
        top_keywords = [feature_names[i] for i in top_indices]
        top_tfidf_scores = [tfidf_scores[i] for i in top_indices]
        return top_keywords, top_tfidf_scores

    results = Parallel(n_jobs=n_jobs)(delayed(process_row)(row) for row in tqdm(X))

    # Sonuçları listelere ayırma
    top_keywords_per_document, top_tfidf_scores_per_document = zip(*results)

    return top_keywords_per_document, top_tfidf_scores_per_document

# Anahtar kelimeleri çıkar ve sonuçları al
# İlk 100 dökümanı işleyin
combined_sample = combined[:400000]
top_keywords_per_document, top_tfidf_scores_per_document = extract_keywords_tfidf(combined_sample, stop_words_list, top_n=10, n_jobs=-1)
#n__jobs ın 2 olması aynı anda iki iş parçacığı yani iki işlem yanı anda yürütülür 
#n__jobs ın -1 olması maksimum işlemci sayısının kullanılmasıdır.

#Sonuçları CSV dosyasına kaydetme
with open('keywords_with_scores.csv', mode='w', newline='', encoding='utf-8') as file:
    writer = csv.writer(file)
    # Başlık satırını yazma
    writer.writerow(['Document_Index'] + [f'Keyword_{i+1}' for i in range(10)] + [f'Score_{i+1}' for i in range(10)])
    
    # Her döküman için anahtar kelimeler ve skorları yazma
    for i, (keywords, scores) in enumerate(zip(top_keywords_per_document, top_tfidf_scores_per_document)):
        row = [i+1] + keywords + [f"{score:.4f}" for score in scores]
        writer.writerow(row)

print("Sonuçlar 'keywords_with_scores.csv' dosyasına kaydedildi.")
"""
# Sonuçları görüntüleme
for i, (keywords, scores) in enumerate(zip(top_keywords_per_document, top_tfidf_scores_per_document)):
    print(f"Döküman {i+1}:")
    for keyword, score in zip(keywords, scores):
        print(f"{keyword}: {score:.4f}")
    print("\n")
"""

  0     1              2                3              4                5    \
0      1992        Hitachi  Football League              6                0   
1                        6                0           None             None   
2      1993  rowspan=""3""   Kashiwa Reysol  rowspan=""2""  Football League   
3      1994              0                0              0                0   
4      1995      J1 League               17              1                2   

             6              7     8     9    ...   204   205   206   207  \
0  colspan=""2""           None  None  None  ...  None  None  None  None   
1           None           None  None  None  ...  None  None  None  None   
2             12              5     1     0  ...  None  None  None  None   
3              0              0     0     0  ...  None  None  None  None   
4              0  colspan=""2""  None  None  ...  None  None  None  None   

    208   209   210   211   212   213  
0  None  None  None  None  N

c:\gitProjects\yeni\.venv\lib\site-packages\sklearn\feature_extraction\text.py:406: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['leh'] not in stop_words.
  warnings.warn(


Buradaki keywords ve skorlar yukarıda çekildi.

In [ ]:
import pandas as pd
import csv

# Anahtar kelimeleri ve TF-IDF skorlarını çekme
top_keywords_per_document, top_tfidf_scores_per_document = extract_keywords_tfidf(combined, stop_words_list, top_n=10, n_jobs=-1)

# Sonuçları tablo şeklinde hazırlama
results_top = []
for keywords, scores in zip(top_keywords_per_document, top_tfidf_scores_per_document):
    row = {}
    for i, (keyword, score) in enumerate(zip(keywords, scores)):
        row[f'Keyword_{i+1}'] = keyword
        row[f'Score_{i+1}'] = score
    results_top.append(row)

# Sonuçları DataFrame'e dönüştürme
df = pd.DataFrame(results_top)

# Sonuçları CSV'ye kaydetme
df.to_csv('keywords_with_scores.csv', index=False, encoding='utf-8')

chunksize = 1000  # Küçük bir parça boyutu belirleyin
for i in range(0, len(df), chunksize):
    df.iloc[i:i+chunksize].to_csv('keywords_with_scores.csv', mode='a', header=(i==0), index=False, encoding='utf-8')

# Sonuçları terminalde görüntüleme
print(df.head())


Encoding yapmak için

In [ ]:
from sentence_transformers import SentenceTransformer

model = SentenceTransformer('sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2')

# Top_keywords embedding
keyword_embeddings = model.encode(top_keywords_per_document)


Text ve keywords similarity denemesi

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

def calculate_keyword_similarity(text, keywords):
    # TF-IDF matrisini oluştur
    tfidf_vectorizer = TfidfVectorizer()

    #texti ve anahtar kelimeleri tf-ıdf vektörlerine dönüştür
    text_tfidf = tfidf_vectorizer.fit_transform([text]) #burayı combined sütunundan almalıyım
    #benzerlik hesaplama 
    similarity_array = []
    for keyword in keywords:
        # Her bir anahtar kelimeyi TF-IDF vektörüne dönüştür
        keyword_tfidf = tfidf_vectorizer.transform([keyword]) #keywordleri teker teker alma fonksiyonu
        
        # Cosine similarity ile benzerlik hesapla
        similarity = cosine_similarity(text_tfidf, keyword_tfidf)[0][0]
        
        # Anahtar kelime ve benzerlik skorunu kaydet
        similarity_array.append((keyword, similarity))
    
    return similarity_array
   

# Örnek metin ve anahtar kelimeler
#combined verileri 


text = "Bu bir örnek metindir ve bu metin üzerinde anahtar kelimeleri test ediyoruz."
keywords = ["başka", "bir", "anahtar", "kelimeleri", "test"] #bu keywordsler tf-değerinden alınarak arraylere çevrilmeli 
    
# Uygunluk skorunu hesapla
similarity_results = calculate_keyword_similarity(text, keywords)
top_5_keywords = sorted(similarity_results, key=lambda x: x[1], reverse=True)[:5]
# Her bir anahtar kelimenin uyumluluk skorunu yazdır

for keyword, similarity in top_5_keywords:
    print(f"Keyword: {keyword}, Similarity: {similarity}")
    #print(f"Keyword: '{keyword}' - Relevance score: {score:.4f}")



In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
# Örnek metin ve anahtar kelimeler
#combined verileri 
def get_text(file_path='processed_data.csv'):
    """CSV dosyasını okur ve veriyi düzenler."""
    with open(file_path, 'r',encoding='utf-8') as file:
        raw_text = file.read()
    
    text = parse_text(raw_text)
    
    # Veri çerçevesi oluştur
    df_text = pd.DataFrame(text)
    
    return df_text

def get_keywords(file_path='keywords_with_scores.csv'):
    """CSV dosyasını okur ve veriyi düzenler."""
    with open(file_path, 'r',encoding='utf-8') as file:
        raw_text = file.read()
    
    keywords = parse_text(raw_text)
    
    # Veri çerçevesi oluştur
    df_keyword = pd.DataFrame(keywords)
    
    return df_keyword


def calculate_keyword_similarity(text, keywords):
    # TF-IDF matrisini oluştur
    tfidf_vectorizer = TfidfVectorizer()

    #texti ve anahtar kelimeleri tf-ıdf vektörlerine dönüştür
    text_tfidf = tfidf_vectorizer.fit_transform(text) #burayı combined sütunundan almalıyım
    #benzerlik hesaplama 
    similarity_array = []
    for keyword in keywords:
        # Her bir anahtar kelimeyi TF-IDF vektörüne dönüştür
        keyword_tfidf = tfidf_vectorizer.transform([keyword]) #keywordleri teker teker alma fonksiyonu
        
        # Cosine similarity ile benzerlik hesapla
        similarity = cosine_similarity(text_tfidf, keyword_tfidf)[0][0]
        
        # Anahtar kelime ve benzerlik skorunu kaydet
        similarity_array.append((keyword, similarity))
    
    return similarity_array
   



    
# Uygunluk skorunu hesapla
similarity_results = calculate_keyword_similarity(text, keywords)
top_5_keywords = sorted(similarity_results, key=lambda x: x[1], reverse=True)[:5]
# Her bir anahtar kelimenin uyumluluk skorunu yazdır

for keyword, similarity in top_5_keywords:
    print(f"Keyword: {keyword}, Similarity: {similarity}")
    #print(f"Keyword: '{keyword}' - Relevance score: {score:.4f}")



In [ ]:

# BERT Tokenizer ve Model'i yükleyin
tokenizer = BertTokenizer.from_pretrained('dbmdz/bert-base-turkish-cased')
model = BertModel.from_pretrained('dbmdz/bert-base-turkish-cased')
# Keywords çıkarma fonksiyonu
def extract_keywords_tfidf(combined_texts, stop_words_list,top_n=5):
    """TF-IDF ile anahtar kelimeleri çıkarır, stop words listesi ile birlikte kullanır."""
    vectorizer = TfidfVectorizer(stop_words=stop_words_list)
    X = vectorizer.fit_transform(combined_texts) #bunu csv den oku 
    feature_names = vectorizer.get_feature_names_out()
    #sorted_keywords = [feature_names[i] for i in X.sum(axis=0).argsort()[0, ::-1]]
    
    top_keywords_per_document = [] #her döküman için en iyi keywordsleri alır
    top_tfidf_scores_per_document = [] #tf-ıdf değeri en yüksek olan dökümanlar
#------------------------------------------------------------------------------------------
    for row in X:
        tfidf_scores = row.toarray().flatten()
        top_indices = tfidf_scores.argsort()[-top_n:][::-1]  # En yüksek n skoru bul
        top_keywords = [feature_names[i] for i in top_indices]
        top_tfidf_scores_per_document = [tfidf_scores[i] for i in top_indices]


        top_tfidf_scores_per_document.append(top_tfidf_scores)
        top_keywords_per_document.append(top_keywords)
        
    return top_keywords_per_document

# Anahtar kelimeleri çıkar ve BERT ile embedding oluştur
def process_texts(combined_texts, stop_words_list,top_n):
    results = []
    
    for text in combined_texts:
        # Anahtar kelimeleri çıkar
        keywords = extract_keywords_tfidf(text, stop_words_list,top_n=15)
        
        # BERT ile embedding oluştur
        inputs = tokenizer(text, return_tensors='pt', truncation=True, max_length=512)
        with torch.no_grad():
            outputs = model(**inputs)
            embeddings = outputs.last_hidden_state.mean(dim=1).squeeze()
        
        results.append({
            'text': text,
            'keywords': keywords,
            'embedding': embeddings
        })
        
    return results

results=process_texts
results
#tüm metinleri işle


MongoDb'den database'in çekilmesi

In [ ]:
#mongodb üzerinden combined_textleri çek
import csv
from pymongo import MongoClient

def mongo_db_combined_texts_to_csv(database_name='combined_text', collection_name='text', host='localhost', port=27017,batch_size=1000,output_file='combined_texts.csv'):
    client = MongoClient(f'mongodb://{host}:{port}/')
    db = client[database_name]
    collection = db[collection_name]
    
    #toplam döküman sayısını al
    total_documents = collection.count_documents({})
    #batch_documents = []

    # CSV dosyasını aç ve yazmaya hazırla
    with open(output_file, mode='w', newline='', encoding='utf-8') as file:
        writer = csv.writer(file)
        writer.writerow(["combined"])  # CSV başlığı

    # Belirtilen batch_size kadar dökümanları almak için döngü
    for i in range(0, total_documents, batch_size):
        cursor = collection.find({}, {"combined":1, "_id": 0}).skip(i).limit(batch_size)
        combined_texts = [doc['combined'] for doc in cursor if 'combined' in doc] #combined sütununa ilişkin verileri çeker 

        # Batch verilerini CSV'ye yaz
        with open(output_file, mode='a', newline='', encoding='utf-8') as file:
            writer = csv.writer(file)
            
            for text in combined_texts:
                writer.writerow([text])
        
        

    print(f"combined metinler '{output_file}' dosyasına başarıyla yazıldı.")

# Dökümanları CSV dosyasına yazdır
text=mongo_db_combined_texts_to_csv(batch_size=1000)
        #batch_documents.extend((combined_texts, len(combined_texts)))
    #append fonksiyonu listenin içerisine tek bir eleman gibi ekler yani list1 = [1, 2, 3, [4, 5]]
    #fakat extend fonksiyonu list1 = [1, 2, 3, 4, 5] bir listeye yeni bir liste eklemeyi teker teker gerçekleştirir.
    #return batch_documents

# Dökümanları ve döküman sayısını batch olarak çekin
#combined_texts = mongo_db_combined_texts(batch_size=1000)

# Her batch'i ayrı ayrı işleyebilirsiniz
#print(f"Toplam döküman sayısı:{len(combined_texts)}")

#for index, text in enumerate (combined_texts[:10]):
    #print(f"Döküman {index + 1}: {text}")

#print(combined_texts)

    

Gereksiz kelimelerin 'gereksiz_kelimeler.txt' üzerinden import edilmesi

TF-IDF Skorları 

In [ ]:
#-----------------------------------------------------------------------------------------------------
# Tüm metinleri işle
combined_texts = mongo_db_combined_texts()
processed_texts = process_texts(combined_texts, stop_words_list,top_n=5)

combined_texts, document_count = mongo_db_combined_texts()
print(f"Toplam döküman sayısı: {document_count}")
print("Combined metinler:", combined_texts)

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

# Text ve keywords
text = """Peynir, çok büyük bir çeşitlilikteki aroma, tat, yapı ve şekle sahip bir grup süt ürünü için kullanılan genel isimdir.

Etimoloji 
Peynir, kelimesi modern Türkçeye Farsça sütten yapılmış manasına gelen panīr kelimesinden geçmiştir. İngilizceye ise Latince caseus dan gelmiştir. Bu kelimenin kökeninin Hint-Avrupa dillerinde yer alan mayalanmak-ekşimek manasına gelen kwat- kökünden geçtiği düşünülmektedir. Bu kelime diğer Cermen dillerinde de muhafaza edilmiştir. İspanyolca ve Portekizce de Latinceden almışlardır ve Malezya ve Endonezya da konuşulan dillere de keşifler vasıtasıyla geçirmişlerdir.

Fransızca, İtalyanca ve Katalancaya ise yine aynı kökenden gelmiş olmasına ragmen, Romalılar tarafından askerlerin tüketimi için yapılan caseus formatus (kalıp peyniri) sözünün ikinci parçası olan kalıp manasına gelen formatusdan türeyen kelimeler kullanılmaya başlanmıştır. İspanyolcada "queso", Portekizcede "queijo", Almancada "Käse", Felemenkçede "Kaas", ve İngilizcede "cheese" İtalyancada "formaggio" olması yanında, Fransızcada "fromage", ve bu terim Katalancada "formatge" olmuştur.

İlk kez Memluk Türkçesinde benir, penir, beynir şekillerinde görülür. Yazılı olarak en eski ÖzTürkçe karşılığı ise Kâşgarlı Mahmud tarafından yazılan Divânu Lügati't-Türk'te geçmektedir; udma ve udhıtma. Udhıtmak Uygur Türkçesi'nde uyutmak anlamındadır ve Udhıtma udhıttı, sütü uyutmak, uyumuş süt, peynir anlamında kullanılmıştır. Farklı Türk lehçelerinde farklı kelimeler kullanılmıştır: ağrımışık, sogut (Karluk), kurut, kesük, çökelek, bışlak.

 Tarihçe 
Peynir kökeni oldukça eskiye dayanan bir yiyecektir. Peynir üretimine dair elde mevcut en eski arkeolojik bulgular M.Ö. 5000 yıllarına aittir ve günümüz Polonya'sında ortaya çıkarılmıştır. Çıkış noktaları Orta Asya, Orta Doğu ya da Avrupa olarak tahmin edilmektedir. Yaygınlaşmasının Roma İmparatorluğu zamanlarında olduğu düşünülür.

İlk üretimi için önerilen tarih MÖ 8. binyıl (koyunun evcilleşitirildiği tarih) ile 9. binyıla kadar değişir. O zamanlar yiyecekleri saklayıcı özelliği nedeniyle hayvanın derisi ya da iç organları kullanılmaktaydı. Bu iç organlardan olan midede (işkembe) saklanan sütün buradaki enzimlerle (kültürle) mayalanması üzerine lor haline gelmesi peynirin ilk oluşumu hakkındaki teorilerden biridir. Buna benzer bir hikâyenin, bir tüccar Arap'ın peynir saklaması hakkında da farklı söylenişleri vardır.Vicki Reich, Cheese January 2002 Newsletter, Moscow Food Co-op Food Info.  

Bir başka teoriyse peynirin sütü tuzlamak ve basınç altında tutma sonucunda ortaya çıktığıdır. Hayvan midesinde bekletilen sütün değişimi üzerine de bu karışıma kasıtlı olarak maya eklenmiş olabilir.

Peynir yapıcılığı ile ilgili ilk yazılı kaynak MÖ 2000'li yıllara, Mısır'daki mezar yazıtlarına dayanmaktadır. Antik zamanlarda yapılan peynirin ekşi ve tuzlu olduğu ve günümüz feta ve beyaz peynire benzediği tahmin edilmektedir.

Avrupa'daki peynir üretiminde ise iklimden dolayı daha az tuz kullanılır. Daha az tuzlu ortamda daha çeşitli faydalı mikrop ve enzim yetişebilmesinden dolayı bu peynirler farklı ve ilginç tatlar içerirler.

 Modern çağ 

Avrupa kültürüyle birlikte yayılmasına kadar peynir, Doğu Asya kültürlerinde ve Kolomb öncesi Amerika'da neredeyse hiç duyulmamıştı ve Akdeniz altı Afrika'da yalnızca sınırlı bir kullanıma sahipti, esasen yalnızca Avrupa, Orta Doğu, Hint altkıtası ve ve bu kültürlerden etkilenen bölgelerde yaygın ve popülerdi. Ancak önce Avrupa emperyalizminin daha sonra da Avrupa-Amerikan kültürünün ve yemeklerinin yayılmasıyla birlikte peynir dünyada giderek daha fazla tanınmaya ve popülerleşmeye başladı.

Peynirin endüstriyel üretimi için ilk fabrika 1815'te İsviçre'de açıldı ancak büyük ölçekli üretim ilk olarak Amerika Birleşik Devletleri'nde gerçek başarıyı yakaladı. Bu başarı genellikle montaj-hattı tarzında komşu çiftliklerden gelen sütü kullanarak 1851'de peynir yapmaya başlayan ve Roma, New York'tan mandıra çiftçisi olan Jesse Williams'a atfedilir. 
Onlarca yıl içinde bu türden yüzlerce süt birlikleri ortaya çıktı.

1860'larda seri üretilen peynir mayası üretimi başladı ve yüzyılın başında bilim adamları saf mikrobiyal kültürler üretiyorlardı. O zamandan önce, peynir yapımındaki bakteriler çevreden veya daha önceki bir partinin peynir altı suyunun geri dönüştürülmesinden geliyordu; saf kültürler, daha standart bir peynirin üretilebileceği anlamına geliyordu.

Fabrika yapımı peynir İkinci Dünya Savaşı döneminde geleneksel peynir yapımını geride bıraktı ve fabrikalar o zamandan beri Amerika ve Avrupa'daki çoğu peynirin kaynağıdır.

Birleşmiş Milletler Gıda ve Tarım Örgütü'ne göre 2004 yılı dünya üzerindeki peynir üretimi 18 milyon ton dur. Bu kahve tanesi, çay yaprağı kakao tanesi ve tütün yıllık üretiminden daha fazladır.

 Üretim 

2014 yılında tam inek sütünden yapılan peynir üretimi dünya’da 18.7 milyon tondu ve Amerika Birleşik Devletleri dünya toplamının %29'u (5.4 milyon ton) peynir üretirken onu büyük üreticiler olarak Almanya, Fransa ve İtalya izledi.

İşlenmiş peynirde diğer 2014 dünya toplamları şunlardı:
 yağsız inek sütünden, 2.4 milyon ton (845,500 ton ile Almanya liderdir)
 keçi sütünden, 523,040 ton (110,750 ton ile Güney Sudan liderdir)
 koyun sütünden, 680,302 ton (125,000 ton ile Yunanistan liderdir)
 manda sütünden, 282,127 ton (254,000 ton Mısır liderdir)

2015 yılında Almanya, Fransa, Hollanda ve İtalya ürettikleri peynirin %10-14'ünü ihraç etti. Amerika Birleşik Devletleri üretiminin çoğunu kendi iç pazarına sattığından ihracatı azdır (toplam inek sütü üretiminin %5.3'ü).

2004 yılına göre en büyük peynir ihracatcısı (parasal değere göre) Fransa olup ikinci Almanya (miktar bakımından birinci olmasına rağmen). En üstteki on ihracatçıdan sadece İrlanda, Yeni Zelanda, Hollanda ve Avustralya ihracat için peynir üretir. Üretimlerinin ihracat yüzdeleri sırasıyla: %95, %90, %72 ve %65 dir. En büyük peynir ihracatçısı Fransa peynir üretiminin sadece %30'unu ihraç eder.

 Tüketim 
Fransa, İzlanda, Finlandiya, Danimarka ve Almanya 2014 yılında kişi başına ortalama  peynir tüketen ülkelerdi.

{| class="wikitable" style="width:30em;"
! colspan=2|En çok peynir tüketen ülkeler - 2003(kişi başına yılık tüketim kg olarak)<ref>{{Web kaynağı |url=http://www.maison-du-lait.com/Scripts/public/stat.asp?Language=GB |başlık=CNIEL |erişimtarihi=20 Eylül 2008 |arşivurl=https://web.archive.org/web/20071006081314/http://www.maison-du-lait.com/Scripts/public/stat.asp?Language=GB |arşivtarihi=6 Ekim 2007 |ölüurl=evet }}</ref>
|-
|  || align="right" | 27.3
|-
|  || align="right" | 24.0
|-
|   || align="right" | 22.9
|-
|  || align="right" | 20.6
|-
|  || align="right" | 20.2
|-
|  || align="right" | 19.9
|-
| || align="right" | 19.5
|-
|  || align="right" | 17.9
|}

 Yapımı 

Peynir, süt proteini kazeinin peynir mayası ve peynir kültürü ile pıhtılaştırılması ve bu pıhtıdan peynir altı suyunun ayrılmasıyla elde edilen fermente bir süt ürünüdür. Buna karşılık kazein yerine peynir altı suyu proteininden oluşan ricotta ve lor gibi peynirler ile peynir mayası içermeyen quark gibi peynirler de vardır. Sütün pH değerinin düşürülmesi için kullanılan peynir kültürü de peynir üretimi için zorunlu olmayıp sitrik asit ve sirke gibi asit içeren maddeler ile sübstitüte edilebilir.

Peynir altı suyu ayrıldıktan sonra tuzlu peynirler için tuzlama aşamasına gelinir. Tuzlama, peynirin yüzeyine kuru tuzlama şeklinde veya peynir salamuraya daldırılarak yapılabilir. Peynir altı suyunun tekrar 90 C°'ye kaynatılması ile lor peynir elde edilir.

Takip eden basamak olgunlaştırmadır; peynir taze olarak tüketilebileceği gibi belirli bir olgunlaştırma periyodunu takiben de tüketilebilir.
Bu üretim basamaklarına ait teknik parametrelere bağlı olarak çok geniş bir çeşitlilikte peynirler elde edilir.

Diğer fermente süt ürünleri gibi peynir de canlı organizmalar içerebilir. Raf ömrü boyunca peynirin duyusal, yapısal ve kimyasal özelliklerinde çeşitli değişiklikler görülebilir. Bu değişikliklerin en az olması için peynirin genellikle 6-8 °C’lik sıcaklıklarda tutulması gereklidir.

Soğuk iklimlerde yaşayanlar için sıcaklığı 6-8 °C civarında, nem oranı sabit ve havadar kilerler peynir saklamak için idealdir. Ancak bu imkânın olmadığı yerde peynir buzdolabının alt raflarında ve kapalı şekilde saklanmalıdır.

 Çeşitleri 

Türkiye'de tüketimi en yaygın olan peynirler; beyaz peynir, deri peyniri ve kaşar peyniri olmakla birlikte, yöresel peynirler yönünden de hayli çeşitlilik gösterir. Bunlardan bazıları:     

 Beslenme ve sağlık 
Peynirin besin değeri çok değişkendir. Süzme peynir %4 yağ ve %11 protein içerebilirken bazı peynir altı suyu peynirleri %15 yağ ve %11 protein ve üçlü krem peynirler %36 yağ ve %7 protein içerir. Genellikle peynir, zengin bir kalsiyum, protein, fosfor, sodyum ve doymuş yağ (Günlük Değer'in %20'si veya daha fazlası) kaynağıdır. 28 gramlık (bir ons) porsiyon çedar peyniri yaklaşık  protein ve 202 miligram kalsiyum içerir. Besinsel olarak peynir esasında konsantre süttür ancak kültür ve yaşlandırma süreçlerince değiştirilir: bu kadar proteini sağlamak için, suda çözünen vitamin ve minerallerin miktarları değişmesine rağmen, yaklaşık  süt ve buna eşit  kalsiyum gerekir.

Sağlıklı hayvan sütlerinden sağlıklı şartlarda üretilen peynirin insan beslenmesine protein, kalsiyum, mineraller ve diğer besin elemanlarının temin edilmesinde ve sağlıklı yaşamın sürdürülmesinde önemli katkıları bulunur. Ancak çiğ sütten yapılan peynirlerden Brucella ve Listeria gibi zoonotik enfeksiyonların tüketenlere bulaşması, ayrıca uygun saklama koşullarına uyulmaması dolayısıyla bakteri üremesine bağlı akut barsak enfeksiyonlarının gelişmesi mümkündür. Tuzlu peynir tüketimi hipertansiyon hastalarında risk oluşturabilir.

Küflü peynir tüketimi

Bazı (yumuşak tip) küflü peynir çeşitlerinin listeria riski dolayısıyla hamilelerde tüketiminin uygun olmadığı, pişirilerek yenmesi durumunda bu sakıncanın ortadan kalkmış olacağı NHS tarafından ifade edilmektedir. Konya'da yöresel olarak tüketilen küflü peynir çeşitleri üzerinde akademik yapılan bir çalışma ile bu peynirlerden elde edilen küf cinsleri, bunların primer ve sekonder metabolitleri, ürettikleri mikotoksinler, aspergillus tipi küflerde ise aflatoksinler gibi kanser yapıcı toksinlerin mevcudiyeti ve zararları ele alınmıştır. Küflü peynirler üzerinde yapılan bir başka çalışmada ise özellikle siyah, beyaz ve kırmızı renkte küf içeren peynir çeşitlerinde aflatoksin miktarının yüksekliğine dikkat çekilmiştir. Bazı mikotoksinlerin DNA hasarı (mutajen) ve fetüs üzerinde sakatlık oluşturma (teratojen) kapasitelerinin olduğu bilinmektedir.http://www.academia.edu/3251581/DUNYADA_VE_TURKIYEDE_INSAN_SAGLIGINI_TEHDIT_EDEN_MIKOTOKSINLERhttp://informahealthcare.com/doi/abs/10.3109/15569549909009258

 Peynirle ilgili kitaplar 
 "Süt Uyuyunca - Türkiye Peynirleri", Artun Ünsal, Yapı Kredi Yayınları, İstanbul, 1. Baskı 1997.
 "Türkiye'nin Peynir Hazineleri* " (Özgün adı: The Treasury of Turkish Cheeses''), Suzanne Swan, Boyut Yayın Grubu, 2005.
 "Yurdumuz Peynirlerini Olgunlaştıran Mikroplar ve Anzimleri", Mehmet Karasoy, Ankara Üniversitesi Veteriner Fakültesi Yay. 1955.
 "Her Yönüyle Peynir", Mehmet Demirci, Hasad Yayıncılık.
 "Türkiye'de Yapılan Muhtelif Tip Peynirler ve Özellikleri", Dilek Uraz - Abdi Karacabey, Ankara, 1974.
 "Peynir", Rauf Cemil Adam, Ege Üniv. Matbaası, 1974.
 "Peynir Teknolojisi Bibliyografyası", Tümer Uraz, Ankara Üniv.
 "Sütçülük, Tereyağcılık ve Peynircilik Sanatları'" (Eski Türkçe), Onnik İhsan, Matbaa-i Âmire, İstanbul, 1915.

Ayrıca bakınız 
 Mandıra ürünü

Notlar 

 
Süt ürünleri
Farsçadan Türkçeye geçen sözcükler"""

keywords = ['peynir', 'peynirin', 'peynirler', 'olarak', 'ton', 'süt', 'avrupa', 'right', 'align', 'yapılan', 'altı', 'üretimi', 'protein', 'büyük', 'elde', 'amerika', 'almanya', 'sütünden', 'fransa', 'dünya', 'farklı', 'küflü', 'ilk', 'kalsiyum', 'çok', 'türkiye', 'peyniri', 'yağ', 'gelen', '20', 'sütü', 'tüketimi', 'tuzlu', 'milyon', 'liderdir', 'olan', 'diğer', 'com', 'doğu', 'daki', 'beyaz', 'devletleri', '2014', 'üzerinde', 'web', 'mayası', 'eski', 'manasına', 'olduğu', 'sağlıklı', 'ortaya', 'www', 'veya', 'tuzlama', 'sütün', 'üretiminin', 'suyu', 'suyunun', 'orta', 'tarafından', 'ankara', 'üretim', 'birleşik', 'lor', 'inek', 'iç', 'göre', 'edilmektedir', 'http', 'üniv', 'üzerine', 'ürünü', '11', '10', '90', '000', 'du', 'dillerinde', 'çeşitli', 'çeşitleri', 'caseus', 'cheese', 'dolayısıyla', 'asit', 'başına', 'asp', 'asya', 'ayrıca', 'üretilen', 'başladı', 'başka', 'besin', 'kaynağıdır', 'kelimeler', 'kalıp', 'yöresel', 'içeren', 'hint', 'ikinci', 'zamandan', 'hollanda', 'günümüz', 'food', 'fermente', 'gb', 'geliyordu', 'fabrika', 'edilen', 'olması', 'olmasına', 'yaygın', 'yapımı', 'olmadığı', 'mısır', 'mö', 'modern', 'maison', 'mandıra', 'nde', 'lk', 'listeria', 'language', 'lait', 'mehmet', 'kullanılmıştır', 'kişi', 'kültürü', 'küf', 'kültürler', 'kullanılan', 'hayvan', 'ilgili', 'içerir', 'ihracat', 'ihraç', 'roma', 'yaklaşık', 'yalnızca', 'peynirleri', 'peynirlerden', 'yapı', 'uraz', 'uyutmak', 'uygun', 'vardır', 'rağmen', 'stanbul', 'scripts', 'yazılı', 'ref', 'proteini', 'public', 'saf', 'te', 'stat', 'sütten', 'türk', 'udhıttı', 'udhıtmak', 'tütün', 'şeklinde', 'üretiyorlardı', 'üretirken', 'üretir', 'üretimlerinin', 'üretimine', 'üretiminden', 'üretiminde', '1860', '1851', '1815']
# TF-IDF vektörizer oluştur
tfidf_vectorizer = TfidfVectorizer()

# Texti ve anahtar kelimeleri TF-IDF vektörlerine dönüştür
text_tfidf = tfidf_vectorizer.fit_transform([text])
keywords_tfidf = tfidf_vectorizer.transform(keywords)

# Benzerlik hesapla
similarities = []
for i in range(keywords_tfidf.shape[0]):
    keyword_tfidf = keywords_tfidf[i, :]
    similarity = cosine_similarity(text_tfidf, keyword_tfidf)
    similarities.append((keywords[i], similarity[0][0]))

# Sonuçları yazdır
for keyword, similarity in similarities:
    #print(f"Keyword: {keyword}, Similarity: {similarity}")

# En yüksek benzerliğe sahip olan ilk 5 anahtar kelimeyi filtrele
    top_5_keywords = sorted(similarities, key=lambda x: x[1], reverse=True)[:5]

# Sonuçları yazdır
for keyword, similarity in top_5_keywords:
    print(f"Keyword: {keyword}, Similarity: {similarity}")

Title değerini bir dataframe' e dönüştürür.

In [4]:
from pymongo import MongoClient
import pandas as pd
import csv

# MongoDB'ye bağlanma

def get_titles(database_name='combined_text', collection_name='text', host='localhost', port=27017,batch_size=1000,output_file='titles_texts.csv'):
    client = MongoClient(f'mongodb://{host}:{port}/')
    db = client[database_name]
    collection = db[collection_name]
    
    #toplam döküman sayısını al
    total_documents = collection.count_documents({})
    #batch_documents = []


    # MongoDB'den sadece title alanlarını çekme
    titles = collection.find({}, {"_id": 0, "title": 1})

    # Verileri liste haline getirme ve DataFrame'e dönüştürme
    df = pd.DataFrame(list(titles))

    
    # CSV dosyasını aç ve yazmaya hazırla
    with open(output_file, mode='w', newline='', encoding='utf-8') as file:
        writer = csv.writer(file)
        writer.writerow(["titles"])  # CSV başlığı

    # Belirtilen batch_size kadar dökümanları almak için döngü
    for i in range(0, total_documents, batch_size):
        cursor = collection.find({}, {"title":1, "_id": 0}).skip(i).limit(batch_size)
        combined_texts = [doc['title'] for doc in cursor if 'title' in doc] #combined sütununa ilişkin verileri çeker 

        # Batch verilerini CSV'ye yaz
        with open(output_file, mode='a', newline='', encoding='utf-8') as file:
            writer = csv.writer(file)
            
            for text in combined_texts:
                writer.writerow([text])
        
        

    print(f"metin başlıkları '{output_file}' dosyasına başarıyla yazıldı.")

    # DataFrame'i görüntüleme
    print(df.head())

# Dökümanları CSV dosyasına yazdır
text=get_titles(batch_size=5000)
        #batch_documents.extend((combined_texts, len(combined_texts)))
    #append fonksiyonu listenin içerisine tek bir eleman gibi ekler yani list1 = [1, 2, 3, [4, 5]]
    #fakat extend fonksiyonu list1 = [1, 2, 3, 4, 5] bir listeye yeni bir liste eklemeyi teker teker gerçekleştirir.
    #return batch_documents

# Dökümanları ve döküman sayısını batch olarak çekin
#combined_texts = mongo_db_combined_texts(batch_size=1000)

# Her batch'i ayrı ayrı işleyebilirsiniz
#print(f"Toplam döküman sayısı:{len(combined_texts)}")

#for index, text in enumerate (combined_texts[:10]):
    #print(f"Döküman {index + 1}: {text}")

#print(combined_texts)

    





metin başlıkları 'titles_texts.csv' dosyasına başarıyla yazıldı.
             title
0    Pşıqo Ahecaqo
1  Craterolophinae
2       Notocrabro
3  Ibrahim Sissoko
4      Salah Cedid


Veri güncelleme 

In [6]:
import pandas as pd

# Örnek TF-IDF skoru ve anahtar kelimeler
keyword_data = pd.read_csv('keywords_with_scores.csv')

df = pd.DataFrame(keyword_data)
print(df.head())


   Document_Index        Keyword_1    Keyword_2      Keyword_3  \
0               1          ahecaqo        pşıqo         çerkes   
1               2  craterolophinae  depastridae  craterolophus   
2               3       notocrabro   crabronina       oymağına   
3               4          sissoko    wolfsburg  panathinaikos   
4               5             baas        cedid          salah   

         Keyword_4    Keyword_5 Keyword_6     Keyword_7  Keyword_8 Keyword_9  \
0         çerkesya         1777  savaşına     lakapları         qo    bjeduğ   
1  altfamilyasıdır        clark      1863       cinsler  taksonomi      2023   
2          cinstir  bağlantılar  kaynakça         ghost     ghetto      ghez   
3        konyaspor    deportivo   étienne        coruña  kiralandı  imzaladı   
4             1970         1993      1926  siyasetçiler  fraksiyon     bitar   

   ... Score_1  Score_2  Score_3  Score_4  Score_5  Score_6  Score_7  Score_8  \
0  ...  0.5162   0.4130   0.3481   0.1903

In [ ]:
import pandas as pd
from langdetect import detect, DetectorFactory

DetectorFactory.seed = 0  # Her zaman aynı sonuçları almak için

def is_turkish(text):
    try:
        return detect(text) == 'tr'
    except:
        return False

def filter_turkish_keywords(text):
    if pd.isna(text):
        return []  # NaN değerleri boş liste olarak döndür
    keywords = text.split(',')  # Anahtar kelimeleri virgülle ayır
    return [kw.strip() for kw in keywords if is_turkish(kw.strip())]

# CSV dosyasını oku
df = pd.read_csv('path_to_your_file.csv')

# Anahtar kelime sütunlarını belirle
keyword_columns = ['Keyword_1', 'Keyword_2', 'Keyword_3', 'Keyword_4', 'Keyword_5', 
                   'Keyword_6', 'Keyword_7', 'Keyword_8', 'Keyword_9', 'Keyword_10']

# Her anahtar kelime sütunu için Türkçe olanları filtrele
for col in keyword_columns:
    df[f'{col}_Turkish'] = df[col].apply(filter_turkish_keywords)

print(df.head())
